# Линейная регрессия

Набор данных содержит информацию о затратах на рекламу (в тыс $) для разных типов медиа: __TV__, __Radio__, __Newspaper__.
 
Результат __Sales__ показывает сколько товаров продано в связи с каждым каналом рекламы (в тыс штук). Собрано 200 наблюдений (рядов). 

In [ ]:
# прочитаем данные из файла в датафрейм pandas
import pandas as pd

example_path = "./advertising.csv"
advertising = pd.read_csv(example_path).drop(['Unnamed: 0'], axis=1) # удалим индекс из csv
print(advertising)

Построим точечный график с помощью графика pandas

In [ ]:

advertising.plot.scatter(x='TV', y='Sales', title='Peклaмa TB')
advertising.plot.scatter(x='Radio', y='Sales', title='Peклaмa Радио')

Построим график с помощью фреймворка matplotlib

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline
# словарь цветов {Class:color(HEX coded)}
colors = {'TV':'#8fcfd1', 'Radio':'#df5e88', 'Newspaper':'#f6ab6c'}

# выберем X
X = advertising[['TV', 'Radio', 'Newspaper']]
# выберем y
y = advertising['Sales']

# реорганизуем колонки
columns = advertising.columns.drop(['Sales'])
# диапазон x (0 to #rows)
x_data = range(0, advertising.shape[0])
# создадим фигуру 800x600 для графика
fig, ax =  plt.subplots(figsize=(8,6))
# построим точечные графики
ax.scatter(x=advertising['TV'], y=advertising['Sales'], color='gold')
ax.scatter(x=advertising['Radio'], y=advertising['Sales'], color='grey')
# заголовок
ax.set_title('Peклaмa- TB / Радио')
# названия осей
ax.set_xlabel('затраты')
ax.set_ylabel('продажи')

## Линейная регрессия

$y = \beta_0 + \beta_1x_1 + \beta_2x_2 + ... + \beta_nx_n + \epsilon $

- $y$ это отклик
- $\beta_0$ это пересечение (intercept)
- $\beta_1$ это коэффициент для $x_1$ фактора 
- $\beta_n$ это коэффициент для $x_n$ фактора
- $\epsilon$ это ошибка модели

Получаем уравнение:

$y = \beta_0 + \beta_1 \times TV + \beta_2 \times Radio + \beta_3 \times Newspaper + \epsilon$

здесь $\beta$ значения называются **коэффициенты модели**. Эти значения вычисляются по критерию наименьших квадратов ошибки (LSE). 

После подбора коэффициентов можно пробовать сделать прогноз по тренду.

Для вычисления коэффициентов можно подключить 
- библиотеку numpy

// Функция polyfit — функция в библиотеке NumPy, которая подгоняет многочлен заданного порядка к набору точек данных с помощью метода наименьших квадратов.

//Функция poly1d создаёт полиномиальную функцию, которую можно использовать для оценки значений многочлена в любой позиции x или построения графика.

- или библиотеку фреймворка [`sklearn.linear_model.LinearRegression()`](https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LinearRegression.html#sklearn.linear_model.LinearRegression).

В sklearn можно получить такое уравнение: $y = 2.88 + 0.0466 \times TV + 0.179 \times Radio + 0.00345 \times Newspaper + \epsilon$

In [ ]:
#import matplotlib.pyplot as plt
import numpy as np

xtv=advertising['TV']
y=advertising['Sales']

fig, ax =  plt.subplots(figsize=(8,6))
# установим вид осей графика
ax.tick_params(direction='in', top=True, right=True)
# рассчитаем линейную регрессию
coefficients = np.polyfit(xtv, y, deg=1)  # наклон, смещение
# создадим функцию тренда
p = np.poly1d(coefficients)
# построим точечный график исходных данных
ax.scatter(xtv, y, label='данные')
# построим график тренда
ax.plot(xtv, p(xtv), label='линейный тренд', color='red')
# добавим текстовую информацию на график
stats = (f'$\\mu$ = {np.mean(y):.2f}\n'
         f'$\\sigma$ = {np.std(y):.2f}\n'
         f'$r$ = {np.corrcoef(xtv, y)[0][1]:.2f}\n'
         f'$y$ = {coefficients[1]:.3f}*x+{coefficients[0]:.3f}' )
# оформим легенду графика
bbox = dict(boxstyle='round', fc='blanchedalmond', ec='orange', alpha=0.5)
ax.text(0.95, 0.07, stats, fontsize=9, bbox=bbox,
        transform=ax.transAxes, horizontalalignment='right')
pass # заглушка вывода сообщения предыдущего оператора


Нарисуем диаграмму матрицы корреляций с помощью библиотеки matplotlib в виде 2D-карты (imshow).

In [ ]:
#import numpy as np
# матрица корреляций (Correlation matrix)
corr = advertising.corr()
fig, ax = plt.subplots(figsize=(6,6))

# тепловая карта (Heatmap)
im = ax.imshow(corr.values, cmap='cividis_r', vmin=0, vmax=1)

# названия по осям
ax.set_xticks(np.arange(len(corr.columns)))
ax.set_yticks(np.arange(len(corr.columns)))
ax.set_xticklabels(corr.columns)
ax.set_yticklabels(corr.columns)
print(corr.values)
# повернем текст на оси x для наглядности
plt.setp(ax.get_xticklabels(), rotation=45, ha="right", rotation_mode="anchor")
pass

Рассмотрим и построим нелинейную зависимость, например, кубический тренд.

In [ ]:
# Perform cubic fit
coefficients = np.polyfit(xtv, y, 3)
print("коэффициенты полинома 3й степени:", coefficients)
print(f'Уравнение тренда = {coefficients[0]:.4f} * X^3 +{coefficients[1]:.4f} * X^2 + {coefficients[2]:.4f} * X + {coefficients[3]:.4f}')

# создадим функцию тренда
polynomial = np.poly1d(coefficients)
# отрисуем данные
plt.scatter(xtv, y, label='данные', color='pink')
# подготовим список из 100 точек по x
xp = np.linspace(0, 300, 100)
# построим кубический тренд
plt.plot(xp, polynomial(xp), label='кубический тренд', color='lime')
plt.legend()
plt.show()

Для получения прогноза по известной функции тренда надо подставить новое знчение x в функцию.

In [ ]:
x_new = [330]
y_new = polynomial(x_new)
print(y_new)